In [1]:
#%%appyter init
from appyter import magic
magic.init(lambda _=globals: _())

In [2]:
import csv
import plotly.offline as py
import plotly.graph_objects as go
import networkx as nx
import matplotlib.pyplot as plt
import pandas as pd
from networkx.algorithms import community
from collections import OrderedDict
import time
import requests
import seaborn as sns
import math
import numpy as np
import os
from pyvis import network as net
import random
import unidecode
import json

In [3]:
%%appyter code_exec

{% do SectionField(
    name="GENES",
    title="Submit a gene list",
) %}



gene_list = {{ TextField(
    name="gene_list",
    label="Gene list",
    description="Paste with a single gene on each line.",
    section="GENES",
    default="",
)}}


n_genes = {{ IntField(
    name="n_genes",
    label="Minimum number of genes per cluster",
    section="GENES",
    default=20,
    minimum=2,
    maximum=1000000
)}}

gene_list_selection = '''{{ ChoiceField(
    name = "gene_list_selection",
    label="Sample gene list to load",
    section="GENES",
    default="SARS-CoV-2_down",
    choices=["SARS-CoV-2_down","ULK4_293_coIP_hits"]
)}}'''

edge_types = {{ MultiCheckboxField(
    name = "edge_types",
    label="Types of edges to use to construct the network",
    section="GENES",
    default=["Gene-gene co-expression","Protein-protein interactions"],
    choices={"Gene-gene co-expression": "Coexpression","Protein-protein interactions": "PPI"}
)}}

sars_list = 5

```python
'''
gene_list = ''''''
'''
n_genes = 20
gene_list_selection = '''SARS-CoV-2_down'''
edge_types = ['Gene-gene co-expression', 'Protein-protein interactions']
sars_list = 5
```

# Load data
---

In [4]:
# Load data
cloud_url = 'https://appyters.maayanlab.cloud/storage/Gene_Network_Analysis/'

In [5]:
print(edge_types)

['Gene-gene co-expression', 'Protein-protein interactions']


In [6]:
# Load sample gene lists

if gene_list_selection == "ULK4_293_coIP_hits":
    with open("ULK4_293_coIP_hits.txt","r") as f_in:
        writer = csv.reader(f_in, lineterminator='\n')
        sample_genes = [item for sublist in writer for item in sublist if len(sublist) > 0]
        gene_lists = [[ x.upper() for x in sample_genes ]]
elif gene_list_selection == "SARS-CoV-2_down":
    df_genes = pd.read_csv(cloud_url + "gene_lists/SARS-CoV-2_down.csv",header=None).drop(columns=[0,1])
    df_genes = df_genes.transpose()
    gene_lists = df_genes.to_dict("list")
    for k,v in gene_lists.items():
        gene_lists[k] = [unidecode.unidecode(x) for x in v if isinstance(x, str)] # filter out NaNs     

In [7]:
print(len(gene_lists))

17


In [202]:
df_ppi_edges = pd.read_csv(cloud_url + 'ppi_edges_list.csv',header=None)
df_gene_edges = pd.read_csv(cloud_url + 'top_500_correlation.csv')

display(df_ppi_edges.head())
print("PPI dataframe shape:", df_ppi_edges.shape)
display(df_gene_edges.head())
print("Gene-gene coexpression dataframe shape:",df_gene_edges.shape)

0         1
0  S100A8   LGALS7B
1  S100A8    IGSF21
2  S100A8       IVL
3  S100A8  SERPINB3
4  S100A8      NCF2

PPI dataframe shape: (282532, 2)


A1BG    A1CF     A2M  A2ML1          A2MP1  A4GALT    A4GNT    AAAS  \
0     ITIH1     PAH   ITIH2    PPL         ARRDC5  ALPPL2  METTL7B   SNRPA   
1      AGXT  SLC2A2    AHSG   TGM1  RP11.927P21.9   KLRG2    SSTR5  RUVBL2   
2   CYP4A11    CPB2  IGFBP1  KLK13       CSPG4P11    FGF4  C2ORF82    PLK1   
3       C8B    APOH   ITIH3   SCEL          SMIM2   NLRP7    KLHL4   CDC20   
4  SLC25A47     ALB     AGT  KRT78   RP11.123K3.4  DNMT3L     SPIC   KIF22   

      AACS   AACSP1  ... ZWILCH     ZWINT           ZXDA         ZXDB  \
0  SLC35E3  TP53I13  ...  CSE1L      MCM6         YBX1P4         CPS1   
1    PEX26    RENBP  ...   NPM1  TIMELESS  RP11.475I24.1      CKAP2P1   
2   ZNF793    PRRT4  ...    RAN     SAA3P           REM2        GLP2R   
3  RPS6KA5     PPOX  ...   LDHB     PSMC5   RP5.1147A1.1  RP11.91J3.1   
4   ZNF556   AQP7P1  ...  PAICS      RFC3          SMCR8       MTNR1A   

       ZXDC  ZYG11A   ZYG11B    ZYX    ZZEF1       ZZZ3  
0      NSA2    CA5A  PPP1R3A  GNAI2   GAREM1     MAP2K6  
1    CICP27  FAM98C    TXLNB  TGFB1   DHRS12      HSBP1  
2  RPL10AP5  PCDHB1     TRDN    PXN  ATP5LP3       POT1  
3   RPL21P3  USHBP1    XIRP2   VASP   GPR162   SNRPGP14  
4   RPL37P1  ZBTB8B     PYGM   SPI1   RPL27A  GOLGA2P2Y  

[5 rows x 26415 columns]

Gene-gene coexpression dataframe shape: (500, 26415)


In [9]:
ppi_edges_dict = {}

for index, row in df_ppi_edges.iterrows():
    if row[0] in ppi_edges_dict:
        ppi_edges_dict[row[0]].append(row[1])
    else:
        ppi_edges_dict[row[0]] = [row[1]]
        
gene_edges_dict = df_gene_edges.to_dict('list')

# Create the networks

In [10]:

'''
def get_relevant_ppi_edges(gene_list):
    edges = []
    for gene in gene_list:
        if gene in ppi_edges_dict:  
            edges = [*edges,  *[(gene, x) for x in ppi_edges_dict[gene]]]
    return edges

def get_relevant_gene_edges(gene_list):
    edges = []
    for gene in gene_list:
        if gene in gene_edges_dict:  
            edges = [*edges,  *[(gene, x) for x in gene_edges_dict[gene]]]
    return edges
'''

def get_relevant_ppi_edges(gene_list):
    edges = []
    missing = []
    for gene_a in gene_list:
        if gene_a in ppi_edges_dict:
            for gene_b in ppi_edges_dict[gene_a]:
                if gene_b == gene_a: continue
                if gene_b in gene_list: edges.append((gene_a, gene_b))      
        else: missing.append(gene_a)
    return edges,missing

def get_relevant_gene_edges(gene_list):
    # use at most the top 3 edges for each gene.
    edges = []
    missing = []
    for gene_a in gene_list:
        gene_count = 0
        if gene_a in gene_edges_dict:
            for gene_b in gene_edges_dict[gene_a]:
                if gene_count >= 3: break 
                if gene_b == gene_a: continue
                if gene_b in gene_list: 
                    gene_count += 1
                    edges.append((gene_a, gene_b))
        else: missing.append(gene_a)
    return edges,missing

def pretty_heading(content):
    num_dashes = len(content) + 2
    num_dashes = max(30,num_dashes)
    print("-"*num_dashes)
    print(content)
    print("-"*num_dashes)    

In [11]:
networks = {}

nums_missing_nodes = []

for list_num, gene_list in gene_lists.items():

    # create the Network object
    pretty_heading(f"Constructing network for gene list {list_num}")
 
    ppi_edges,ppi_missing = get_relevant_ppi_edges(gene_list)
    gene_edges,gene_missing = get_relevant_gene_edges(gene_list)
    
    print("Missing PPI nodes:\n\n", ppi_missing, "\n")
    print("Missing gene-gene co-expression nodes:\n\n", gene_missing, "\n")
    
    both_missing = set(ppi_missing).intersection(set(gene_missing))
    print("Missing nodes for both types of edges:\n\n", both_missing, "\n")
        
    G = nx.Graph(name=list_num)
    G.add_nodes_from(gene_list)
    
    if "Protein-protein interactions" in edge_types:
        G.add_edges_from(ppi_edges,edge_type="PPI")

    if "Gene-gene co-expression" in edge_types:
        G.add_edges_from(gene_edges,edge_type="Coexpression")
        
    hits = []
    
    for edge in G.edges:
        hits.append(edge[0])
        hits.append(edge[1])
        
    num_missing = len(gene_list) - len(list(set(hits)))
    print(num_missing, " disconnected or missing nodes\n")
    nums_missing_nodes.append(num_missing)
  
    print(nx.info(G), "\n")
    
    networks[list_num] = G
    
    

    


--------------------------------------
Constructing network for gene list 0
--------------------------------------
Missing PPI nodes:

 ['RNU5B-1', 'SMIM30', 'OTUD6B-AS1', 'MNS1', 'UQCRHL', 'MT1E', 'TMEM60', 'AC078927.1', 'AL138752.2', 'LOC107984142', 'NDUFC1', 'COX16', 'AC005083.1', 'NEIL3', 'CLTRN', 'RPL36A-HNRNPH2', 'YBX1P10', 'RN7SL832P', 'CHCHD2P2', 'ARL 14.00', 'AL445685.3', 'SYNJ2BP-COX16', 'GATA6-AS1', 'PSMC1P1', 'AC134682.1', 'TMEM229B', 'AC124045.1', 'AC073548.1', 'TCN1', 'TMEM156', 'CYSTM1', 'FDCSP', 'H1-5', 'PPM1N', 'SNHG6', 'H2AC11', 'C11orf58', 'IQCK', 'SMIM20', 'SLCO1B3', 'PET100', 'RETREG1', 'H3P6', 'PYURF', 'NEDD8-MDP1', 'AC116533.1', 'EIF2S2P4', 'OCIAD2', 'TSPAN13', 'PLAAT4', 'BRD7P2', 'IFI27L2', 'RPS28P7', 'CFAP298-TCP10L', 'ATP5F1E', 'AL021546.1', 'H3C12', 'ATP5MC3', 'SELENOT', 'AL645922.1', 'ELL2P1', 'ANXA2P2', 'AC097625.2', 'CCDC152', 'MIR1244-1', 'FAIM', 'CT83', 'AC099661.1', 'RPL24P4', 'GLYATL2', 'ABRACL', 'COX6A1', 'NDUFC2', 'COX7B', 'TSTD1', 'ANKRD22', 'LIPA',

Missing PPI nodes:

 ['MYOM3', 'ABHD2', 'THAP5', 'SLC35B2', 'ANKRD50', 'MARS2', 'FAXDC2', 'CEACAM7', 'HCG8', 'CLMN', 'CEMIP', 'SNHG8', 'MT-ATP6', 'SMIM13', 'COL27A1', 'UCA1', 'LOC101929128', 'FAM114A1', 'TMEM170A', 'C12ORF75', 'SERINC5', 'NDNF', 'SOS 1', 'KRT42P', 'LOC101927391', 'C4ORF3', 'NPTN', 'PNCK', 'HPDL', 'LOC105377924', 'SLC5A3', 'SNHG1', 'MUC17', 'NYNRIN', 'OLMALINC', '6-Sep', 'ADPRHL1', 'RETNLB', 'XXYLT1', 'TMEM69', 'LINC01559', 'C1ORF43', 'TOP 1.00', 'RASAL1', 'ADGRF1', 'CNNM1', 'ARL 14.00', 'SLC44A4', 'ACAP2', 'CROCCP2', 'ACER2', 'PIGZ', 'C2ORF42', 'LHFPL2', 'ASAH2B', 'OXR1', 'SETD9', 'KIAA0101', 'EPB41L4A-AS1', 'OR2A4', 'C3ORF62', 'JMJD8', 'ZNF717', '3-Mar', 'B3GALNT2', 'BRWD3', 'ZNF337-AS1', 'USP34', 'FER1L4', 'TMCC1', 'FA2H', 'TCN1', 'NCBP2-AS2', 'HPF1', 'LINC01057', 'FABP6', 'C17ORF100', 'ZNF641', 'LOC644794', 'SSUH2', 'FEM1C', 'CLCA4', 'C6ORF223'] 

Missing gene-gene co-expression nodes:

 ['MT-CYB', 'MT-ND4', 'HCG8', 'SNHG8', 'MT-ATP6', 'UCA1', 'LOC101929128', 'MT-ND

Missing PPI nodes:

 ['WDR81', 'C19ORF47', 'IER5L', 'SAPCD2', 'PRR15', 'DDX12P', 'PIF1', 'TMEM160', 'LRRC14', 'NSDHL', 'PCDH9', 'DISP2', 'SLC25A39', 'C1ORF116', 'ZNF672', 'MPV17L2', 'SLC39A3', 'ZNF787', 'C21ORF58', 'METRN', 'HNF1A-AS1', 'TMPO-AS1', 'MPC2', 'C1QTNF6', 'CYB5B', 'HMGCS1', 'SP9', 'KCNK5', 'C1ORF159', 'MROH6', 'DGCR6', 'MMAB', 'KIAA0895L', 'ZBTB45', 'PRADC1', 'INSL4', 'CD320', 'BRI3BP', 'SLC35A4', 'KRT4', 'JMJD8', 'SLC23A1', 'HS6ST1', 'PAQR4', 'SNHG10', 'KLHDC7A', 'CCDC96', 'MLF 2.00', 'TPPP3', 'RPUSD1', 'ZDHHC12', 'NUBP2', 'ARHGEF39', 'BOP 1.00', 'PRR15L', 'TMEM104', 'MUC13', 'TICRR', 'HPDL', 'TMEM201', 'MFSD3', 'SLC22A18AS', 'IGFBPL1'] 

Missing gene-gene co-expression nodes:

 ['HLA-DMB', 'HNF1A-AS1', 'TMPO-AS1', 'SNHG10', 'MLF 2.00', 'BOP 1.00'] 

Missing nodes for both types of edges:

 {'BOP 1.00', 'SNHG10', 'HNF1A-AS1', 'MLF 2.00', 'TMPO-AS1'} 

6  disconnected or missing nodes

Name: 9
Type: Graph
Number of nodes: 500
Number of edges: 1777
Average degree:   7.1080 


# Compute clusters
---

In [12]:
# Clustering
all_clusters = {}

### k-clique communities

In [231]:
all_clusters["k_clique_communities"] = {}

for num, G in networks.items():

    pretty_heading(f"Computing k_clique_communities for gene list {num}")
    
    c = list(community.k_clique_communities(G, 3)) 
    clusters = [ list(x) for x in c if len(x) > n_genes]
    print(f"Computed {len(clusters)} cluster(s)\n")
    
    print("Cluster sizes:", [len(x) for x in clusters],"\n")

    all_clusters["k_clique_communities"][num] = clusters

------------------------------------------------
Computing k_clique_communities for gene list 0
------------------------------------------------
Computed 1 cluster(s)

Cluster sizes: [254] 

------------------------------------------------
Computing k_clique_communities for gene list 1
------------------------------------------------
Computed 4 cluster(s)

Cluster sizes: [102, 74, 32, 27] 

------------------------------------------------
Computing k_clique_communities for gene list 2
------------------------------------------------
Computed 4 cluster(s)

Cluster sizes: [119, 25, 27, 22] 

------------------------------------------------
Computing k_clique_communities for gene list 3
------------------------------------------------
Computed 3 cluster(s)

Cluster sizes: [37, 159, 32] 

------------------------------------------------
Computing k_clique_communities for gene list 4
------------------------------------------------
Computed 3 cluster(s)

Cluster sizes: [141, 26, 21] 

-----

### Girvan-Newman communities

In [232]:
all_clusters["girvan_newman"] = {}

for num, G in networks.items():
    pretty_heading(f"Computing girvan_newman communities for gene list {num}")

    communities_generator = community.girvan_newman(G)
    top_level_communities = next(communities_generator)
    next_level_communities = next(communities_generator)
    clusters = [ list(x) for x in next_level_communities if len(x) > n_genes ]
    clusters = [ list(x) for x in clusters if len(x) > n_genes]
    print(f"Computed {len(clusters)} cluster(s)\n") 
    print("Cluster sizes:", [len(x) for x in clusters],"\n")
    #print(clusters)
    
    all_clusters["girvan_newman"][num] = clusters

-----------------------------------------------------
Computing girvan_newman communities for gene list 0
-----------------------------------------------------
Computed 2 cluster(s)

Cluster sizes: [385, 29] 

-----------------------------------------------------
Computing girvan_newman communities for gene list 1
-----------------------------------------------------
Computed 3 cluster(s)

Cluster sizes: [369, 51, 50] 

-----------------------------------------------------
Computing girvan_newman communities for gene list 2
-----------------------------------------------------
Computed 2 cluster(s)

Cluster sizes: [327, 145] 

-----------------------------------------------------
Computing girvan_newman communities for gene list 3
-----------------------------------------------------
Computed 2 cluster(s)

Cluster sizes: [437, 36] 

-----------------------------------------------------
Computing girvan_newman communities for gene list 4
-------------------------------------------------

### Greedy modularity communities

In [233]:
all_clusters["greedy_modularity_communities"] = {}

for num, G in networks.items():
    pretty_heading(f"Computing greedy_modularity_communities for gene list {num}")

    clusters = list(community.greedy_modularity_communities(G))
    clusters = [ list(x) for x in clusters if len(x) > n_genes]
    
    print(f"Computed {len(clusters)} cluster(s)\n") 
    print("Cluster sizes:", [len(x) for x in clusters],"\n")
    
    all_clusters["greedy_modularity_communities"][num] = clusters



---------------------------------------------------------
Computing greedy_modularity_communities for gene list 0
---------------------------------------------------------
Computed 6 cluster(s)

Cluster sizes: [113, 111, 87, 46, 40, 21] 

---------------------------------------------------------
Computing greedy_modularity_communities for gene list 1
---------------------------------------------------------
Computed 8 cluster(s)

Cluster sizes: [129, 105, 61, 50, 38, 27, 26, 21] 

---------------------------------------------------------
Computing greedy_modularity_communities for gene list 2
---------------------------------------------------------
Computed 8 cluster(s)

Cluster sizes: [118, 77, 55, 53, 43, 39, 28, 28] 

---------------------------------------------------------
Computing greedy_modularity_communities for gene list 3
---------------------------------------------------------
Computed 7 cluster(s)

Cluster sizes: [96, 85, 79, 71, 54, 42, 26] 

---------------------------

In [234]:
all_clusters["connected_components"] = {}
# connected_components

for num, G in networks.items():
    pretty_heading(f"Computing connected_components for gene list {num}")
    
    components = sorted(nx.connected_components(G), key = len, reverse=True)
    clusters = [ list(x) for x in components if len(x) > n_genes ]

    print(f"Computed {len(clusters)} cluster(s)\n") 
    print("Cluster sizes:", [len(x) for x in clusters],"\n")
    
    all_clusters["connected_components"][num] = clusters



------------------------------------------------
Computing connected_components for gene list 0
------------------------------------------------
Computed 1 cluster(s)

Cluster sizes: [422] 

------------------------------------------------
Computing connected_components for gene list 1
------------------------------------------------
Computed 1 cluster(s)

Cluster sizes: [470] 

------------------------------------------------
Computing connected_components for gene list 2
------------------------------------------------
Computed 1 cluster(s)

Cluster sizes: [477] 

------------------------------------------------
Computing connected_components for gene list 3
------------------------------------------------
Computed 1 cluster(s)

Cluster sizes: [482] 

------------------------------------------------
Computing connected_components for gene list 4
------------------------------------------------
Computed 1 cluster(s)

Cluster sizes: [474] 

---------------------------------------------

### Compile all clustering results

In [235]:
all_cluster_dfs = {}

clustering_results = []

for clustering_method, gene_lists in all_clusters.items():
    for num, clusters in gene_lists.items():
        for index,cluster in enumerate(clusters):
            for gene in cluster:
                data = {"gene": gene, "gene_list": num, "clustering_method": clustering_method, "cluster": index}     
                clustering_results.append(data)
df_clusters = pd.DataFrame(clustering_results)

display(df_clusters)  

gene  gene_list     clustering_method  cluster
0       WDR54          0  k_clique_communities        0
1      NDUFC1          0  k_clique_communities        0
2       PYURF          0  k_clique_communities        0
3       FANCL          0  k_clique_communities        0
4       PSMA2          0  k_clique_communities        0
...       ...        ...                   ...      ...
26907  SH3RF2         16  connected_components        0
26908  LRRCC1         16  connected_components        0
26909  BCKDHB         16  connected_components        0
26910   SFRP5         16  connected_components        0
26911    SGO1         16  connected_components        0

[26912 rows x 4 columns]

# Network visualizations
---

In [236]:
# generate colors to color code clusters
def random_color():
    hex_number = "#000000"
    while hex_number == "#000000":
        hex_number = "#"+''.join([random.choice('0123456789ABCDEF') for j in range(6)])
    return hex_number

cluster_color_dict = {}
edge_color_dict = {"PPI": "#bd34eb", "Coexpression": "#2dc2b0"}

def color_by_cluster(cluster):
    if not cluster in cluster_colors:
        cluster_color_dict[cluster] = random_color()
    return cluster_color_dict[cluster]

In [243]:
# networkx and plotly code
def network_graph(num, G, df):
 
    pos = nx.spring_layout(G,k=1,iterations=800)
    for n, p in pos.items():
        G.nodes[n]['pos'] = p

    edge_x = {"PPI": [], "Coexpression": []}
    edge_y = {"PPI": [], "Coexpression": []}

    for edge in G.edges.data():
        x0, y0 = G.nodes[edge[0]]['pos']
        x1, y1 = G.nodes[edge[1]]['pos']

        edge_type = edge[2]['edge_type']
        edge_x[edge_type].append(x0)
        edge_x[edge_type].append(x1)
        edge_x[edge_type].append(None)
        edge_y[edge_type].append(y0)
        edge_y[edge_type].append(y1)
        edge_y[edge_type].append(None)

    ppi_edge_trace = go.Scatter(
        x=edge_x["PPI"], y=edge_y["PPI"],
        line=dict(width=1, color=edge_color_dict["PPI"]),
        hoverinfo='none',
        mode='lines',
        name="Protein-protein interaction")

    coexp_edge_trace = go.Scatter(
        x=edge_x["Coexpression"], y=edge_y["Coexpression"],
        line=dict(width=1, color=edge_color_dict["Coexpression"]),
        hoverinfo='none',
        mode='lines',
        name="Gene-gene coexpression")

    # dicts mapping clusters to relevant node info
    node_x = {}
    node_y = {}
    gene_names = {}
    
    cluster_node_data = {}
    cluster_node_data["not assigned"] = {"x": [], "y": [], 'color': "#c5d0d1", 'genes': []}

    for node in G.nodes():
        cluster = df[df["gene"] == node]["cluster"].values
        if len(cluster) > 0:
            cluster = cluster[0]
            if cluster not in cluster_node_data:
                cluster_node_data[cluster] = {
                    'x': [], 
                    'y': [], 
                    'color': "", #color_by_cluster(cluster), 
                    'genes': []
                }
        else:
            cluster = "not assigned"

        x, y = G.nodes[node]['pos']
        cluster_node_data[cluster]['x'].append(x)
        cluster_node_data[cluster]['y'].append(y)
        cluster_node_data[cluster]['genes'].append(node)
        
    
    cluster_node_data_sorted = {k: v for k, v in sorted(cluster_node_data.items(),
                                                       key= lambda x: str(x)) if k != 'not assigned'}
    cluster_node_data_sorted['not assigned'] = cluster_node_data['not assigned']
    
    node_traces = []
    for cluster, data in cluster_node_data_sorted.items():
        trace = go.Scatter(
                    x=data['x'], 
                    y=data['y'],
                    mode='markers',
                    hoverinfo='text',
                    text=data['genes'],
                    name=str(cluster),
                    textposition='middle center',
                    marker=dict(
                        showscale=False,
                        reversescale=True,
                        size=10,
                        line_width=2))
        if cluster == 'not assigned':
            trace.marker.color = data['color']
        
        node_traces.append(trace)

    fig = go.Figure(
        data=[ppi_edge_trace, coexp_edge_trace, *node_traces],
        layout=go.Layout(
            title=f"Gene list {num}, {df['clustering_method'].values[0]}<br>",
            titlefont_size=16,
            showlegend=True,
            hovermode='closest',
            margin=dict(b=10,l=5,r=5,t=40),
            xaxis=dict(showgrid=False, zeroline=False, showticklabels=False),
            yaxis=dict(showgrid=False, zeroline=False, showticklabels=False)))
    fig.show()


In [244]:
for num, G in networks.items():
    clustering_coeff = nx.average_clustering(G)
    print("Average clustering: ",clustering_coeff)
    for clustering_method in df_clusters['clustering_method'].unique():
        if not clustering_method == 'greedy_modularity_communities': continue
        df_method = df_clusters[df_clusters["clustering_method"] == clustering_method]
        df_method = df_method[df_method["gene_list"] == num] 
        #display(df_method)

        network_graph(num,G,df_method)

Average clustering:  0.23162437804439812


Average clustering:  0.253789864407857


Average clustering:  0.27193136783224947


Average clustering:  0.23026106254188347


Average clustering:  0.20554560250593346


...

Average clustering:  0.2561571025402745


Average clustering:  0.23574347721927189


Average clustering:  0.2641313737232088


Average clustering:  0.21461962295031994


Average clustering:  0.21097054000430418


# Validation of cluster quality with Enrichr scores
---

In [ ]:
# Validation with Enrichr
enrichr_libraries = OrderedDict([
    ('Ontologies', ['GO_Biological_Process_2018']),
])

# Util functions
def enrichr_link_from_genes(genes, description='', enrichr_link='https://amp.pharm.mssm.edu/Enrichr'):
    ''' Functional access to Enrichr API
    '''
    time.sleep(1)
    resp = requests.post(enrichr_link + '/addList', files={
    'list': (None, '\n'.join(genes)),
    'description': (None, description),
    })
    if resp.status_code != 200:
        raise Exception('Enrichr failed with status {}: {}'.format(
          resp.status_code,
          resp.text,
        ))
    # wait a tinybit before returning link (backoff)
    time.sleep(1)
    result = resp.json()
    return dict(result, link=enrichr_link + '/enrich?dataset=' + resp.json()['shortId'])

def enrichr_get_top_results(userListId, bg, enrichr_link='https://amp.pharm.mssm.edu/Enrichr'):
    time.sleep(1)
    resp = requests.get(enrichr_link + '/enrich?userListId={}&backgroundType={}'.format(userListId, bg))
    if resp.status_code != 200:
        raise Exception('Enrichr failed with status {}: {}'.format(
          resp.status_code,
          resp.text,
        ))
    time.sleep(1)
    return pd.DataFrame(resp.json()[bg], columns=['rank', 'term', 'pvalue', 'zscore', 'combinedscore', 'overlapping_genes', 'adjusted_pvalue', '', ''])


In [ ]:
# Get Enrichr links for each method, for each gene list, for each cluster
enrichr_links = {}

for clustering_method, cluster_groups in all_clusters.items():
    enrichr_links[clustering_method] = {}
    for num, clusters in cluster_groups.items():
        enrichr_links[clustering_method][num]  = {}
        for index, genes in enumerate(clusters):
            try:
                link = enrichr_link_from_genes(genes, f'gene list {num}, {clustering_method} cluster {index}')
            except:
                link = None
                print(f'Enrichr failed for {clustering_method}, cluster {index} genes')

            enrichr_links[clustering_method][num][index] = link

In [ ]:
top_n_results = 5
num_overall_results = 100
sort_by = 'combinedscore'

# Grab top results for each cluster
all_enrichr_results = []

for clustering_method, cluster_groups in enrichr_links.items():
    if clustering_method == 'overall': continue
    for num, links in cluster_groups.items():
        num_clusters = len(all_clusters[clustering_method][num])
        if num_clusters == 0: continue
        top_n_results = int(num_overall_results / num_clusters)
        for cluster, link in links.items():
            if link is None:
                continue
            for category, libraries in enrichr_libraries.items():
                for library in libraries:
                    try:
                        results = enrichr_get_top_results(link['userListId'], library).sort_values(sort_by).iloc[:top_n_results]
                        results['clustering_method'] = clustering_method
                        results['gene_list'] = num
                        results['link'] = link['link']
                        results['library'] = library
                        results['category'] = category
                        results['cluster'] = cluster
                        all_enrichr_results.append(results)
                    except:
                        print('{}: {} {} {} gene list {} cluster {} failed, continuing'.format(link, library, category, clustering_method, num, cluster))

df_clustering_results = pd.concat(all_enrichr_results).reset_index()

In [ ]:
display(df_clustering_results)
print(sort_by)

In [ ]:
unique_terms = {}
num_unique_terms = []

num_unique_hits = []

for clustering_method in [ x for x in df_clustering_results["clustering_method"].unique() if x != "overall"]:
    df_method = df_clustering_results.loc[df_clustering_results["clustering_method"] == clustering_method]
    
    terms = df_method["term"].values    
    unique = list(set(terms))
    num_unique_terms.append(len(unique))
    unique_terms[clustering_method] = unique
    
    hits = df_method.shape[0]
    num_unique_hits.append(hits)



# avg number of unique terms per method
avg_unique_terms = int(np.mean(np.array(num_unique_terms)))
print("Average unique terms per clustering method: ", avg_unique_terms)

# avg number of enrichr entries per method
avg_hits = int(np.mean(np.array(num_unique_hits)))
print("Average hits per clustering method: ", avg_hits)

In [ ]:
# get data on the overall gene sets

overall_results = []
num_results = int(avg_hits / len(gene_lists))
for num, genes in gene_lists.items():
    for category, libraries in enrichr_libraries.items():
        for library in libraries:
            try:
                link = enrichr_link_from_genes(genes, 'overall')
                results = enrichr_get_top_results(link['userListId'], library).sort_values(sort_by).iloc[:top_n_results]
                results['gene_list'] = num
                results['clustering_method'] = 'overall'
                results['link'] = link['link']
                results['library'] = library
                results['category'] = category
                results['cluster'] = ""
                overall_results.append(results)
            except:
                print('Failed to get Enrichr results for overall gene set')

In [ ]:
df_clustering_results = pd.concat(all_enrichr_results).reset_index()

In [ ]:
df_overall_results = pd.concat(overall_results)

df_overall_results = df_overall_results.loc[:,[ x for x in df_overall_results.columns if x != ""]]

df_clustering_results = df_clustering_results.loc[:,[ x for x in df_clustering_results.columns if x != ""]]

df_enrichr_results = pd.concat([df_overall_results,df_clustering_results]).reset_index()

In [ ]:
# accumulate results for each method
neg_log_pvalues = {}
combined_scores = {}

for clustering_method in df_enrichr_results["clustering_method"].unique():
    df_method = df_enrichr_results.loc[df_enrichr_results["clustering_method"] == clustering_method]
    vals = df_method["pvalue"].values
    neg_log_pvalues[clustering_method] = [ -math.log(p) for p in vals]
    combined_scores[clustering_method] = df_method["combinedscore"].values

In [ ]:
# accumulate results for each cluster
neg_log_pvalues_cluster = {}
combined_scores_cluster = {}

for clustering_method in df_enrichr_results["clustering_method"].unique():
    df_method = df_enrichr_results.loc[df_enrichr_results["clustering_method"] == clustering_method]
    for cluster in df_method["cluster"].unique():
        df_cluster = df_method[df_method["cluster"] == cluster]
        vals = df_cluster["pvalue"].values
        neg_log_pvalues[f'{clustering_method}_cluster_{cluster}'] = [ -math.log(p) for p in vals]
        combined_scores[f'{clustering_method}_cluster_{cluster}'] = df_cluster["combinedscore"].values

In [ ]:
# plot one distribution per method

for clustering_method, y in neg_log_pvalues.items():
    fig, ax = plt.subplots()
    #print(len(y))
    sns.distplot(y, ax=ax, label=clustering_method)
    ax.set_title(clustering_method)
    ax.set_xlabel("-log (p-value)")
    ax.set_ylabel("Frequency")
    plt.xlim([-1,10])  

In [ ]:
# plot one distribution per cluster

for cluster, y in neg_log_pvalues_cluster.items():
    fig, ax = plt.subplots()
    #print(len(y))
    sns.distplot(y, ax=ax, label=cluster)
    ax.set_title(cluster)
    ax.set_xlabel("-log (p-value)")
    ax.set_ylabel("Frequency")
    plt.xlim([-1,10])  

In [ ]:
# Overlay the kernel density estimates of combined scores on a single plot
sns.set(color_codes=True)

for clustering_method, y in combined_scores.items():
    print(len(y))
    fig, ax = plt.subplots(figsize=(7,5))
    sns.kdeplot(y, neg_log_pvalues[clustering_method], label=clustering_method,shade=True)
    ax.set_title(clustering_method)
    ax.set_xlabel("Combined score")
    ax.set_ylabel("-log(p-value)")
    ax.legend()


In [ ]:
# Overlay the kernel density estimates of combined scores on a single plot
# for each cluster

for cluster, y in combined_scores_cluster.items():
    print(len(y))
    fig, ax = plt.subplots(figsize=(7,5))
    sns.kdeplot(y, neg_log_pvalues_cluster[cluster], label=cluster,shade=True)
    ax.set_title(cluster)
    ax.set_xlabel("Combined score")
    ax.set_ylabel("-log(p-value)")
    ax.legend()

In [ ]:
'''
cluster_colors = {}
edge_colors = {"PPI": "#bd34eb", "Coexpression": "#2dc2b0"}

os.makedirs("network_visualizations/PPI_and_coexpression_graphs",exist_ok=True)
os.makedirs("network_visualizations/PPI",exist_ok=True)
os.makedirs("network_visualizations/coexpression",exist_ok=True)

folder = "./network_visualizations/"

if len(edge_types) == 2:
    folder += "PPI_and_coexpression_graphs"
elif "Protein-protein interactions" in edge_types:
    folder += "PPI"
elif "Gene-gene co-expression" in edge_types:
    folder += "coexpression"

# make the clustering method graphs
for num, G in networks.items():
    for clustering_method in df_clusters.clustering_method.unique():
        
        df_method = df_clusters[df_clusters["clustering_method"] == clustering_method]
        df_method = df_method[df_method["gene_list"] == num]
    
        nt = net.Network(width="100%", height = 800, notebook=True)
        nt.from_nx(G)
        # nt.show_buttons()
        for node in nt.nodes:
            cluster = df_method[df_method["gene"] == node["id"]]
            if cluster.shape[0] == 0: node["color"] = "#000"
            else: 
                #print(cluster)
                cluster_num = cluster["cluster"].values[0]
                if not cluster_num in cluster_colors:
                    cluster_colors[cluster_num] = random_color()
                
                node["color"] = cluster_colors[cluster_num]
                
        for edge in nt.edges:
            edge["color"] = edge_colors[edge["edge_type"]]
            edge["title"] = edge["edge_type"]
        nt.prep_notebook()
        display(f"Gene list {num}, {clustering_method}")
        display(nt.show(f"{folder}/graph_{num}_{clustering_method}.html"))
'''



# Comparison to [STRING](https://string-db.org) results

In [ ]:
# comparison to STRING results

string_api_url = "https://string-db.org/api"
output_format = "json"
method = "interaction_partners"

request_url = "https://string-db.org/api/json/network"
nums_misses_string = []

for num, genes in gene_lists.items():
    params = {
        "identifiers" : "%0d".join(genes), # your protein
        "species": 9606
    }
    
    hits = set()
    
    response = requests.post(request_url, data=params)
    data = response.json()
    for interaction in data:
        hits.add(interaction["preferredName_A"])
        hits.add(interaction["preferredName_B"])
    
    misses = set()
    
    for gene in gene_list:
        if gene not in hits:
            misses.add(gene)
    
    print(f"{len(genes) - len(hits)} gene misses out of {len(genes)}\n")
    nums_misses_string.append(len(genes) - len(hits))      

In [ ]:
# Compare missing/disconnected nodes in our network to those in STRING

%matplotlib inline
gene_list_nums = [str(x) for x in gene_lists.keys()]
gene_list_sizes = [len(v) for k,v in gene_lists.items()]

fig, ax = plt.subplots(figsize=(10,7))

bar1 = plt.bar(gene_list_nums,nums_misses_string,label="STRING misses",color="#")
bar2 = plt.bar(gene_list_nums,nums_missing_nodes, label="Our misses",color="#")
ax.set_ylabel("Number of disconnected nodes")
ax.set_xlabel("Gene list")
ax.legend()
plt.show()

In [ ]:
print(num_misses_string)
print(num_misses)